In that bachelor thesis I'm comparing a classification model with  a classification after regression. In order to do this I didive the data into train and test sets. From the given list[(101, 32), (101,256),(101,512), (101,768)
                         ,(300,32),(300,256), (300,512),(300,768),(500,32),
                        (500,256),(500,512),(500,768)](first parametr is n_estimators, second parametr is max_features) I'm choosing one optimal parametr for each model.For finding optimal parametrs I'm using a cross-validation.  Then I'm using that choosen parametr in order to make models learn for the whole train set.And all this I repeat 5x. In the end of those codes you can find the result table. 

In [1]:
import pandas as pd
from rdkit import Chem
from rdkit.Chem import AllChem
from rdkit.Chem import Draw
import numpy as np
from rdkit.Chem import Draw
from sklearn.ensemble import RandomForestClassifier
from sklearn.datasets import make_classification
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import LogisticRegression
from sklearn import preprocessing
from sklearn.metrics import classification_report
from sklearn.model_selection import cross_val_score
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.model_selection import KFold
from sklearn.model_selection import ShuffleSplit
from sklearn.svm import SVC
import sklearn.metrics as metrics
import scikitplot as skplt
import matplotlib.pyplot as plt
from sklearn.metrics import roc_curve, roc_auc_score
from sklearn.datasets import load_wine
from sklearn.ensemble import RandomForestRegressor
from sklearn.datasets import make_regression
from sklearn.metrics import precision_recall_curve
import seaborn as sns; sns.set()
from sklearn.metrics import mean_squared_error

RDKit WARNING: [15:09:30] Enabling RDKit 2019.09.3 jupyter extensions


In [2]:
data = pd.read_csv('LXRb_ch25_curated_DW_2.csv')

data_new = data.copy()    # copy raw data
data_new["Molecule"] = [Chem.MolFromSmiles(mol) for mol in data["smiles"]]   #create new column

#colmun['Molecule'] invert to binary systems
data_new['bin'] = [np.array(AllChem.GetMorganFingerprintAsBitVect(i,2, nBits=1024)) for i in data_new['Molecule']]
print("All data which i have:",len(data_new))

All data which i have: 1080


In [3]:

filter_large = data_new['category'] == 'active'     #how many molecules are active
print("Active data:",len(data_new.loc[filter_large]))
filter_large = data_new['category'] == 'inactive'   # how many molecules are inactive
print("Inactive data:",len(data_new.loc[filter_large]))

Active data: 335
Inactive data: 745


Divide data into two sets: test and train in the ratio 80:20.
This operation is repeated 5 times,to get 5 different sets

In [5]:
def divide_the_data_into_two_sets():
    #stratification divide(80:20) data for train and test set
    train, test = train_test_split(data_new, test_size=0.2, shuffle=True, stratify = data_new['category'])
    display(len(test))
    print("Have many train set", len(train))
    filter_large = test['category'] == 'active'
    print("Active test set",len(test.loc[filter_large]))
    filter_large = test['category'] == 'inactive'
    print("Inactive in test set",len(test.loc[filter_large]))
    filter_large = train['category'] == 'active'
    print("Active train set",len(train.loc[filter_large]))
    filter_large = train['category'] == 'inactive'
    print("Inactive in train set",len(train.loc[filter_large]))
    display(test['chembl_id'][:10])
    return train, test

In [11]:
x,y = divide_the_data_into_two_sets()


216

Have many train set 864
Active test set 67
Inactive in test set 149
Active train set 268
Inactive in train set 596


519     CHEMBL225884
574     CHEMBL248900
84     CHEMBL1351761
587     CHEMBL249926
251    CHEMBL1507474
951     CHEMBL454596
661    CHEMBL3196832
378    CHEMBL1712093
352    CHEMBL1602553
508     CHEMBL217118
Name: chembl_id, dtype: object

This function(cross_validation_of_all_models) will make a cross validation
Using these parameters for the function [(101, 32), (101,256),(101,512), (101,768)
                         ,(300,32),(300,256), (300,512),(300,768),(500,32),
                        (500,256),(500,512),(500,768)](first parametr is n_estimators, second parametr is max_features) for the frame parameter is different random_state
                        
With this function I will find the optimal parameters for tree model( classification[case1], regression[case2.1] and classification after regression[case2.2])
Which I then use on train test

In [51]:
#END table of all model
def cross_validation_of_all_models(thre, X, y):
    n_splits = 5    
    #category_new is column where have convert category(inactive/active) to (0,1)
    X['category_new'] = np.where(X['pec50']>=thre, 1, 0)
    y['category_new'] = np.where(y['pec50']>=thre, 1, 0)
    
    kf = KFold(n_splits = n_splits, shuffle=True, random_state=20)
    a = -1   
    
    #for cykl for different paramtrs
    for n_est, max_f in [(101, 32), (101,256),(101,512), (101,768)
                        ,(300,32),(300,256), (300,512),(300,768),(500,32),
                        (500,256),(500,512),(500,768)]:
        #for cykl for random state 
        for ran in [10,20,30,40,50]:
            #for cyklus fot splits(5 splits)
            a = 0
            for trains, valids in kf.split(X):
                a = a+1
                train = X.iloc[trains]   
                valid = X.iloc[valids]
        
                #CLASSIFICATION, i used bin and category new columns   
                case = 1
                x_train = np.asarray([x for x in train['bin']])
                x_valid = np.asarray([x for x in valid['bin']]) 
                y_train = np.asarray([y for y in train['category_new']])
                y_valid = np.asarray([y for y in valid['category_new']])
    
                rfc = RandomForestClassifier(n_estimators=n_est,max_features=max_f, max_depth=4, random_state=ran)
                rfc.fit(x_train,y_train)
                rfc_predict = rfc.predict(x_valid)
                conf_matrix = confusion_matrix(y_valid, rfc_predict)
                #TN, FP, FN, TP = conf_matrix.ravel()
                accur = metrics.accuracy_score(y_valid, rfc_predict)
                #print(accur)
    
                if(accur == 1):
                    TPR = 1
                    TNR = 1
                    MCC = 1
                else:
                    TN, FP, FN, TP = conf_matrix.ravel()
                    # Sensitivity
                    TPR = TP/(TP+FN)
                    # Specificity 
                    TNR = TN/(TN+FP)
                    #MCC
                    MCC = ((TP*TN)-(FP*FN))/((TP+FP)*(FN+TN)*(FP+TN)*(TP+FN))**(1/2)
    
                
                #add data for pandas table
                try:
                    pomoc = {'Case':[case],'threshold': [thre],'Split':[a],'N_est':[n_est],'Max_f':[max_f],'Random_state':[ran],'Accuracy':[accur], 'Sensitiv.':[TPR], 'Specif.':[TNR], 'MCC':[MCC]}
                    df_table = pd.DataFrame(data=pomoc)

                    data_out_end = data_out_end.append(df_table, ignore_index = True)
                    data_out_end.drop_duplicates(keep='first', inplace=True)
                except:
                    pomoc = {'Case':[],'threshold': [],'Split':[],'N_est':[],'Max_f':[],'Random_state':[],'Accuracy':[], 'Sensitiv.':[], 'Specif.':[], 'MCC':[]}
                    data_out_end = pd.DataFrame(data=pomoc)
                    pomoc = {'Case':[case],'threshold': [thre],'Split':[a],'N_est':[n_est],'Max_f':[max_f],'Random_state':[ran],'Accuracy':[accur], 'Sensitiv.':[TPR], 'Specif.':[TNR], 'MCC':[MCC]}
                    df_table = pd.DataFrame(data=pomoc)

                    data_out_end = data_out_end.append(df_table, ignore_index = True)
                    data_out_end.drop_duplicates(keep='first', inplace=True)

        

                #REGRESSION i used bin and pec50  
                case = 2.1
                x_train_reg = [f for f in train['bin']]
                x_valid_reg = [f for f in valid['bin']]
                y_train_reg = [a for a in train['pec50']]
                y_valid_reg = [a for a in valid['pec50']]
                data_new_reg_x = [i for i in X['bin']]
                
                rfr = RandomForestRegressor(n_estimators=n_est,max_features=max_f,max_depth=4, random_state=ran)
                rfr.fit(x_train_reg, y_train_reg)
                y_pred_x = rfr.predict(x_valid_reg)
                y_pred = rfr.predict(data_new_reg_x)
               
                X['pec50_new'] = y_pred
                
                
                #Find the optimal parameter for regresia I will find using error
                error = metrics.mean_squared_error(y_valid_reg, y_pred_x)
                try:
                    pomocc = {'Case':[case],'threshold': [thre],'Split':[a],'N_est':[n_est],'Max_f':[max_f],                            'Random_state':[ran],'Error':[error]}
                    dff_table = pd.DataFrame(data=pomocc)

                    data_out_reg = data_out_reg.append(dff_table, ignore_index = True)
                    data_out_reg.drop_duplicates(keep='first', inplace=True)
                except:
                    pomocc = {'Case':[],'threshold': [],'Split':[],'N_est':[],'Max_f':[],'Random_state':[],                             'Error':[]}
                    data_out_reg= pd.DataFrame(data=pomocc)
                    pomocc = {'Case':[case],'threshold': [thre],'Split':[a],'N_est':[n_est],'Max_f':[max_f],                            'Random_state':[ran],'Error':[error]}
                    dff_table = pd.DataFrame(data=pomocc)

                    data_out_reg = data_out_reg.append(dff_table, ignore_index = True)
                    data_out_reg.drop_duplicates(keep='first', inplace=True)
                
                #CLASSIFICATION AFTER REGRESSION i used bin and category_new_reg
                case = 2.2
                X['category_new_reg'] = np.where(X['pec50_new']>=thre, 1, 0)
                train = X.iloc[trains]
                valid = X.iloc[valids]
               
                x_train_cl = np.asarray([x for x in train['bin']])
                x_valid_cl = np.asarray([x for x in valid['bin']]) 
                y_train_cl = np.asarray([y for y in train['category_new_reg']])
                y_valid_cl = np.asarray([y for y in valid['category_new_reg']])
    
                rfc_reg = RandomForestClassifier(n_estimators=n_est,max_features=max_f, max_depth=4, random_state=ran)
                rfc_reg.fit(x_train_cl,y_train_cl)
                rfc_reg_predict = rfc_reg.predict(x_valid_cl)
                conf_matrix = confusion_matrix(rfc_reg_predict, y_valid_cl)
                accur = metrics.accuracy_score(y_valid_cl, rfc_reg_predict)
               # print(accur)
               
                if(accur == 1):
                    TPR = 1
                    TNR = 1
                    MCC = 1
                else:
                    TN, FP, FN, TP = conf_matrix.ravel()
                    # Sensitivity
                    TPR = TP/(TP+FN)
                    # Specificity 
                    TNR = TN/(TN+FP)
                    #MCC
                    MCC = ((TP*TN)-(FP*FN))/((TP+FP)*(FN+TN)*(FP+TN)*(TP+FN))**(1/2)
    
                try:
                    pomoc = {'Case':[case],'threshold': [thre],'Split':[a],'N_est':[n_est],'Max_f':[max_f],'Random_state':[ran],'Accuracy':[accur], 'Sensitiv.':[TPR], 'Specif.':[TNR], 'MCC':[MCC]}
                    df_table = pd.DataFrame(data=pomoc)

                    data_out_end = data_out_end.append(df_table, ignore_index = True)
                    data_out_end.drop_duplicates(keep='first', inplace=True)
                except:
                    pomoc = {'Case':[],'threshold': [],'Split':[],'N_est':[],'Max_f':[],'Random_state':[],'Accuracy':[], 'Sensitiv.':[], 'Specif.':[], 'MCC':[]}
                    data_out_end = pd.DataFrame(data=pomoc)
                    pomoc = {'Case':[case],'threshold': [thre],'Split':[a],'N_est':[n_est],'Max_f':[max_f],'Random_state':[ran],'Accuracy':[accur], 'Sensitiv.':[TPR], 'Specif.':[TNR], 'MCC':[MCC]}
                    df_table = pd.DataFrame(data=pomoc)

                    data_out_end = data_out_end.append(df_table, ignore_index = True)
                    data_out_end.drop_duplicates(keep='first', inplace=True)
            
    #sort data for Caseand Threshold
    data_out_end = data_out_end.sort_values(by=['Case', 'threshold'])
    data_out_reg = data_out_reg.sort_values(by=['Case', 'threshold'])
    #display(data_out_reg)
    
    #Mean 
    table_prumer_pro_split = data_out_end.groupby(['Case', 'N_est', 'Max_f']).mean()
    table_prumer_reg = data_out_reg.groupby(['Case', 'N_est', 'Max_f']).mean()
  
    
    #now, i find opt_parametr for reggression model
    #print("Table for regression")
    opt_parametr_reg = table_prumer_reg.min(level = 0)
    table_prumer_reg = table_prumer_reg.reset_index()
    #display(opt_parametr_reg)
    #display(table_prumer_reg)
    pomocc = {'Case':[],'threshold': [],'Split':[],'N_est':[],'Max_f':[],'Random_state':[],'Error':[]}
    result_reg = pd.DataFrame(data=pomocc)
    for x in opt_parametr_reg['Error']:
        graf = table_prumer_reg[table_prumer_reg.Error == x] 
        result_reg = result_reg.append(graf)
    #print("RESULR_REG opt_aramter")
    #display(result_reg)
    result_reg = result_reg.drop(columns=['Split', 'Random_state', 'Error']) 

    #print("Table_prumumerna pro kazdy parametr:")
    #display(table_prumer_pro_split)
    table_prumer = table_prumer_pro_split.copy()
    opt_parametr = table_prumer.max(level = 0)

    table_prumer = table_prumer.reset_index()
    #print("Opt_parametr for all model")
    #display(opt_parametr)
    
    pomoc = {'Case':[],'threshold': [],'Split':[],'N_est':[],'Max_f':[],'Random_state':[],'Accuracy':[], 'Sensitiv.':[], 'Specif.':[], 'MCC':[]}
    result = pd.DataFrame(data=pomoc)
    for x in opt_parametr['MCC']:
        graf = table_prumer[table_prumer.MCC == x] 
        result = result.append(graf)
        
   # print("Vysledna tabulka kde jsou opt_ pramametry pro Classification model")
    result = result.drop(columns=['Split', 'Random_state', 'Accuracy', 'Sensitiv.', 'Specif.'])
   
    #display(result)
    result = result.drop(columns=['MCC'])
    #сейчас у нас есть оптимальные параметры, теперь нужно их использовать на общее данные на Х множину
    
    result = result.append(result_reg)
    result = result.sort_values(by=['Case', 'threshold'])
    
    result.index = np.arange(len(result))
    print("Optimal parametrs for all metods")
    display(result)
    #posledni upravz tadz , chci dve funkce udelat v jedne!!!!!!!!
    opt_param_n_est = result['N_est']
    opt_param_max_f = result['Max_f']
    arr = bez_cross_val(opt_param_n_est, opt_param_max_f)
    return result,arr
   


this function(bez_cross_val) doing Random Forest with optimal paramtr for all train set


In [52]:
def bez_cross_val(opt_param_n_est, opt_param_max_f):    
    a = -1
    opt_param_n_est = opt_param_n_est.astype('int')
    opt_param_max_f = opt_param_max_f.astype('int')
    opt_param_n_est_1 = opt_param_n_est[0]   #opt_param n_est for Clessification model 
    opt_param_max_f_1 = opt_param_max_f[0]  #opt_param max_f for Clessification model 
    
    x_train = np.asarray([x for x in X['bin']])
    x_test = np.asarray([x for x in y['bin']]) 
    y_train = np.asarray([y for y in X['category_new']])
    y_test = np.asarray([y for y in y['category_new']])
    for ran in [10,20,30,40,50]:
        
        a += 1
        #RANDOM FOREST
        case = 1        
        rfc = RandomForestClassifier(n_estimators=opt_param_n_est_1,
                                     max_features=opt_param_max_f_1, max_depth=4, random_state=ran)
        rfc.fit(x_train,y_train)
        rfc_predict = rfc.predict(x_test)
        conf_matrix = confusion_matrix(y_test, rfc_predict)
       # TN, FP, FN, TP = conf_matrix.ravel()    
        accur = metrics.accuracy_score(y_test, rfc_predict)
        #print(accur)
    
        if(accur == 1):            
            TPR = 1
            TNR = 1
            MCC = 1
        else:
            TN, FP, FN, TP = conf_matrix.ravel()
            # Sensitivity
            TPR = TP/(TP+FN)
            # Specificity 
            TNR = TN/(TN+FP)
            #MCC
            MCC = ((TP*TN)-(FP*FN))/((TP+FP)*(FN+TN)*(FP+TN)*(TP+FN))**(1/2)
        try:
            pomoc = {'threshold': [thre],'Case':[case],'Split':[a],'N_est':[opt_param_n_est_1],'Max_f':[opt_param_max_f_1],'Random_state':[ran],'Accuracy':[accur], 'Sensitiv.':[TPR], 'Specif.':[TNR], 'MCC':[MCC]}
            df_table = pd.DataFrame(data=pomoc)

            data_out_end = data_out_end.append(df_table, ignore_index = True)
            data_out_end.drop_duplicates(keep='first', inplace=True)
        except:
            pomoc = {'threshold': [],'Case':[],'Split':[],'N_est':[],'Max_f':[],'Random_state':[],'Accuracy':[], 'Sensitiv.':[], 'Specif.':[], 'MCC':[]}
            data_out_end = pd.DataFrame(data=pomoc)
            pomoc = {'threshold': [thre],'Case':[case],'Split':[a],'N_est':[opt_param_n_est_1],'Max_f':[opt_param_max_f_1],'Random_state':[ran],'Accuracy':[accur], 'Sensitiv.':[TPR], 'Specif.':[TNR], 'MCC':[MCC]}
            df_table = pd.DataFrame(data=pomoc)
            data_out_end = data_out_end.append(df_table, ignore_index = True)
            data_out_end.drop_duplicates(keep='first', inplace=True)
        
    
     
      
        #case 2.1 Regression! zatim pouziju parametry obzcejneho classifikation
        case = 2.1
        opt_param_n_est_2 = opt_param_n_est[1]  #opt_param n_est for Regression  model
        opt_param_max_f_2 = opt_param_max_f[1]   #opt_param max_f for Regression model
        x_train_reg = [f for f in X['bin']]
        x_test_reg = [f for f in y['bin']]
        y_train_reg = [a for a in X['pec50']]
        y_test_reg = [a for a in y['pec50']]
        
        data_new_reg_x = [i for i in X['bin']]
        data_new_reg_y = [i for i in y['bin']]
        rfr = RandomForestRegressor(n_estimators=opt_param_n_est_2,max_features=opt_param_max_f_2, max_depth=4, random_state=ran)
        rfr.fit(x_train_reg, y_train_reg)
        
        x_pred = rfr.predict(data_new_reg_x)
        X['pec50_new'] = x_pred
        y_pred = rfr.predict(data_new_reg_y)
        y['pec50_new'] = y_pred
    
    
    
        #case 2.2 Clasification after regression
        case = 2.2
        opt_param_n_est = opt_param_n_est.astype('int')
        opt_param_max_f = opt_param_max_f.astype('int')
        opt_param_n_est_3 = opt_param_n_est[2]    #opt_param n_est for Classification after Regression  model
        opt_param_max_f_3 = opt_param_max_f[2]    #opt_param max_f for Classification after Regression  model
    
        X['category_new_reg'] = np.where(X['pec50_new']>=thre, 1, 0)
        y['category_new_reg'] = np.where(y['pec50_new']>=thre, 1, 0)
        x_train = np.asarray([x for x in X['bin']])
        x_test = np.asarray([x for x in y['bin']]) 
        y_train = np.asarray([y for y in X['category_new_reg']])
        y_test = np.asarray([y for y in y['category_new_reg']])
    
        rfc = RandomForestClassifier(n_estimators=opt_param_n_est_3,max_features=opt_param_max_f_3, max_depth=4, random_state=ran)
        rfc.fit(x_train,y_train)
        rfc_predict = rfc.predict(x_test)
        conf_matrix = confusion_matrix(y_test, rfc_predict)
        #TN, FP, FN, TP = conf_matrix.ravel()
    
        accur = metrics.accuracy_score(y_test, rfc_predict)
        #print(accur)
    
        if(accur == 1):
            TPR = 1
            TNR = 1
            MCC = 1
        else:
            TN, FP, FN, TP = conf_matrix.ravel()
            # Sensitivity
            TPR = TP/(TP+FN)
            # Specificity 
            TNR = TN/(TN+FP)
            #MCC
            MCC = ((TP*TN)-(FP*FN))/((TP+FP)*(FN+TN)*(FP+TN)*(TP+FN))**(1/2)
    
        try:
            pomoc = {'threshold': [thre],'Case':[case],'Split':[a],'N_est':[opt_param_n_est_3],
                     'Max_f':[opt_param_max_f_3],'Random_state':[ran],'Accuracy':[accur], 'Sensitiv.':[TPR], 'Specif.':[TNR], 'MCC':[MCC]}
            df_table = pd.DataFrame(data=pomoc)

            data_out_end = data_out_end.append(df_table, ignore_index = True)
            data_out_end.drop_duplicates(keep='first', inplace=True)
        except:
            pomoc = {'threshold': [],'Case':[],'Split':[],'N_est':[],'Max_f':[],'Random_state':[],'Accuracy':[], 'Sensitiv.':[], 'Specif.':[], 'MCC':[]}
            data_out_end = pd.DataFrame(data=pomoc)
            pomoc = {'threshold': [thre],'Case':[case],'Split':[a],'N_est':[opt_param_n_est_3],'Max_f':[opt_param_max_f_3],'Random_state':[ran],'Accuracy':[accur], 'Sensitiv.':[TPR], 'Specif.':[TNR], 'MCC':[MCC]}
            df_table = pd.DataFrame(data=pomoc)

            data_out_end = data_out_end.append(df_table, ignore_index = True)
            data_out_end.drop_duplicates(keep='first', inplace=True)
            
        data_out_end = data_out_end.sort_values(by=['Case', 'threshold'])
   
    data_out_end = data_out_end.groupby(['Case']).mean()
    
    
    return data_out_end

In [53]:

def diferent_thre(thre):
    

    opt_param1, arr1 = cross_validation_of_all_models(thre, X, y)
    number = 1


    result_table = pd.DataFrame({'Number':[number],'thre':[thre],'Opt_param_class(N_est)':[opt_param1['N_est'][0]],
                              'Opt_param_class(Max_f)':[opt_param1['Max_f'][0]],'MCC(clas.)':[arr1['MCC'][1.0]],
                              'Opt_param_cl_after_reg(N_est)':[opt_param1['N_est'][2]],
                              'Opt_param_cl_after_reg(Max_f)':[opt_param1['Max_f'][2]],
                              'MCC(class_after_reg.)':[arr1['MCC'][2.2]]})

    display(result_table)


    number = 2
    
    
    opt_param2, arr2 = cross_validation_of_all_models(thre, X2, y2)
    result_table2 = pd.DataFrame({'Number':[number],'thre':[thre],'Opt_param_class(N_est)':[opt_param2['N_est'][0]],
                              'Opt_param_class(Max_f)':[opt_param2['Max_f'][0]], 'MCC(clas.)':[arr2['MCC'][1.0]],
                             'Opt_param_cl_after_reg(N_est)':[opt_param2['N_est'][2]],
                              'Opt_param_cl_after_reg(Max_f)':[opt_param2['Max_f'][2]],
                             'MCC(class_after_reg.)':[arr2['MCC'][2.2]]})
    result_table = result_table.append(result_table2, ignore_index = True)
    display(result_table)
    
    number = 3
    
    
    opt_param3, arr3 = cross_validation_of_all_models(thre, X3, y3)
    result_table3 = pd.DataFrame({'Number':[number], 'thre':[thre],'Opt_param_class(N_est)':[opt_param3['N_est'][0]],
                              'Opt_param_class(Max_f)':[opt_param3['Max_f'][0]],'MCC(clas.)':[arr3['MCC'][1.0]],
                              'Opt_param_cl_after_reg(N_est)':[opt_param3['N_est'][2]],
                              'Opt_param_cl_after_reg(Max_f)':[opt_param3['Max_f'][2]],
                              'MCC(class_after_reg.)':[arr3['MCC'][2.2]]})
    result_table = result_table.append(result_table3, ignore_index = True)
    display(result_table)


    number = 4
    

    opt_param4, arr4 = cross_validation_of_all_models(thre, X4, y4)
    result_table4 = pd.DataFrame({'Number':[number],'thre':[thre],'Opt_param_class(N_est)':[opt_param4['N_est'][0]],
                              'Opt_param_class(Max_f)':[opt_param4['Max_f'][0]], 'MCC(clas.)':[arr4['MCC'][1.0]],
                              'Opt_param_cl_after_reg(N_est)':[opt_param4['N_est'][2]],
                              'Opt_param_cl_after_reg(Max_f)':[opt_param4['Max_f'][2]],
                              'MCC(class_after_reg.)':[arr4['MCC'][2.2]]})
    result_table = result_table.append(result_table4, ignore_index = True)
    display(result_table)



    number = 5
    

    opt_param5, arr5 = cross_validation_of_all_models(thre, X5, y5)
    result_table5 = pd.DataFrame({'Number':[number],'thre':[thre],'Opt_param_class(N_est)':[opt_param5['N_est'][0]],
                              'Opt_param_class(Max_f)':[opt_param5['Max_f'][0]], 'MCC(clas.)':[arr5['MCC'][1.0]],
                              'Opt_param_cl_after_reg(N_est)':[opt_param5['N_est'][2]],
                              'Opt_param_cl_after_reg(Max_f)':[opt_param5['Max_f'][2]],
                              'MCC(class_after_reg.)':[arr5['MCC'][2.2]]})
    result_table = result_table.append(result_table5, ignore_index = True)



    print("Result_table")
    display(result_table)
    return result_table
X, y = divide_the_data_into_two_sets()
X2, y2 = divide_the_data_into_two_sets()
X3, y3 = divide_the_data_into_two_sets()
X4, y4 = divide_the_data_into_two_sets()
X5, y5 = divide_the_data_into_two_sets()
c = diferent_thre(6)
a = diferent_thre(5)
b = diferent_thre(5.5)

d = diferent_thre(6.5)
e = diferent_thre(7)

frames = [a, b, c, d, e]
result_t = pd.concat(frames)
result_t.index = np.arange(len(result_t))
display(result_t)


216

Have many train set 864
Active test set 67
Inactive in test set 149
Active train set 268
Inactive in train set 596


899     CHEMBL400121
921     CHEMBL422904
569     CHEMBL243531
66     CHEMBL1340332
31     CHEMBL1300723
205    CHEMBL1466899
589     CHEMBL250129
463     CHEMBL210990
507     CHEMBL216055
796    CHEMBL3809850
Name: chembl_id, dtype: object

216

Have many train set 864
Active test set 67
Inactive in test set 149
Active train set 268
Inactive in train set 596


...

Case  threshold  N_est  Max_f
0   1.0        7.0  300.0  512.0
1   2.1        7.0  500.0  512.0
2   2.2        7.0  101.0   32.0
3   2.2        7.0  300.0   32.0
4   2.2        7.0  500.0   32.0

/home/valeriia/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:70: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/valeriia/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:72: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/valeriia/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: 

Result_table


Number  thre  Opt_param_class(N_est)  Opt_param_class(Max_f)  MCC(clas.)  \
0       1     7                   300.0                   512.0    0.776149   
1       2     7                   101.0                   768.0    0.750827   
2       3     7                   101.0                   768.0    0.726769   
3       4     7                   300.0                   768.0    0.794888   
4       5     7                   300.0                   512.0    0.776149   

   Opt_param_cl_after_reg(N_est)  Opt_param_cl_after_reg(Max_f)  \
0                          101.0                           32.0   
1                          101.0                           32.0   
2                          101.0                           32.0   
3                          101.0                           32.0   
4                          101.0                           32.0   

   MCC(class_after_reg.)  
0               0.791760  
1               0.812526  
2               0.791760  
3               0.810986  
4               0.791760

Number  thre  Opt_param_class(N_est)  Opt_param_class(Max_f)  MCC(clas.)  \
0        1   5.0                   500.0                    32.0    0.807880   
1        2   5.0                   500.0                    32.0    0.806623   
2        3   5.0                   101.0                    32.0    0.798916   
3        4   5.0                   300.0                    32.0    0.796601   
4        5   5.0                   500.0                    32.0    0.807880   
5        1   5.5                   300.0                   256.0    0.859249   
6        2   5.5                   300.0                    32.0    0.797512   
7        3   5.5                   500.0                    32.0    0.794055   
8        4   5.5                   300.0                    32.0    0.784671   
9        5   5.5                   500.0                   512.0    0.848035   
10       1   6.0                   101.0                   256.0    0.809642   
11       2   6.0                   500.0                   256.0    0.821197   
12       3   6.0                   500.0                   256.0    0.818176   
13       4   6.0                   500.0                   256.0    0.838954   
14       5   6.0                   500.0                   256.0    0.818176   
15       1   6.5                   300.0                   768.0    0.734591   
16       2   6.5                   300.0                   512.0    0.784237   
17       3   6.5                   500.0                   512.0    0.782623   
18       4   6.5                   101.0                   512.0    0.797827   
19       5   6.5                   500.0                   256.0    0.791441   
20       1   7.0                   300.0                   512.0    0.776149   
21       2   7.0                   101.0                   768.0    0.750827   
22       3   7.0                   101.0                   768.0    0.726769   
23       4   7.0                   300.0                   768.0    0.794888   
24       5   7.0                   300.0                   512.0    0.776149   

    Opt_param_cl_after_reg(N_est)  Opt_param_cl_after_reg(Max_f)  \
0                           101.0                          768.0   
1                           500.0                          768.0   
2                           300.0                          768.0   
3                           500.0                          512.0   
4                           300.0                          768.0   
5                           500.0                          256.0   
6                           101.0                          256.0   
7                           500.0                          256.0   
8                           500.0                          256.0   
9                           500.0                          256.0   
10                          101.0                          512.0   
11                          500.0                          256.0   
12                          500.0                          512.0   
13                          500.0                          512.0   
14                          500.0                          256.0   
15                          500.0                          256.0   
16                          300.0                           32.0   
17                          300.0                          256.0   
18                          300.0                           32.0   
19                          300.0                          768.0   
20                          101.0                           32.0   
21                          101.0                           32.0   
22                          101.0                           32.0   
23                          101.0                           32.0   
24                          101.0                           32.0   

    MCC(class_after_reg.)  
0                0.776967  
1                0.807232  
2                0.793566  
3                0.859882  
4             

In [56]:
result_t.to_csv('result_table_ba2.csv', encoding='utf-8')
result_t

Number  thre  Opt_param_class(N_est)  Opt_param_class(Max_f)  MCC(clas.)  \
0        1   5.0                   500.0                    32.0    0.807880   
1        2   5.0                   500.0                    32.0    0.806623   
2        3   5.0                   101.0                    32.0    0.798916   
3        4   5.0                   300.0                    32.0    0.796601   
4        5   5.0                   500.0                    32.0    0.807880   
5        1   5.5                   300.0                   256.0    0.859249   
6        2   5.5                   300.0                    32.0    0.797512   
7        3   5.5                   500.0                    32.0    0.794055   
8        4   5.5                   300.0                    32.0    0.784671   
9        5   5.5                   500.0                   512.0    0.848035   
10       1   6.0                   101.0                   256.0    0.809642   
11       2   6.0                   500.0                   256.0    0.821197   
12       3   6.0                   500.0                   256.0    0.818176   
13       4   6.0                   500.0                   256.0    0.838954   
14       5   6.0                   500.0                   256.0    0.818176   
15       1   6.5                   300.0                   768.0    0.734591   
16       2   6.5                   300.0                   512.0    0.784237   
17       3   6.5                   500.0                   512.0    0.782623   
18       4   6.5                   101.0                   512.0    0.797827   
19       5   6.5                   500.0                   256.0    0.791441   
20       1   7.0                   300.0                   512.0    0.776149   
21       2   7.0                   101.0                   768.0    0.750827   
22       3   7.0                   101.0                   768.0    0.726769   
23       4   7.0                   300.0                   768.0    0.794888   
24       5   7.0                   300.0                   512.0    0.776149   

    Opt_param_cl_after_reg(N_est)  Opt_param_cl_after_reg(Max_f)  \
0                           101.0                          768.0   
1                           500.0                          768.0   
2                           300.0                          768.0   
3                           500.0                          512.0   
4                           300.0                          768.0   
5                           500.0                          256.0   
6                           101.0                          256.0   
7                           500.0                          256.0   
8                           500.0                          256.0   
9                           500.0                          256.0   
10                          101.0                          512.0   
11                          500.0                          256.0   
12                          500.0                          512.0   
13                          500.0                          512.0   
14                          500.0                          256.0   
15                          500.0                          256.0   
16                          300.0                           32.0   
17                          300.0                          256.0   
18                          300.0                           32.0   
19                          300.0                          768.0   
20                          101.0                           32.0   
21                          101.0                           32.0   
22                          101.0                           32.0   
23                          101.0                           32.0   
24                          101.0                           32.0   

    MCC(class_after_reg.)  
0                0.776967  
1                0.807232  
2                0.793566  
3                0.859882  
4             

In [2]:
result = pd.read_csv('result_table_ba2.csv')
display(result)
result = result.drop(columns=['Number','Unnamed: 0','Opt_param_class(N_est)', 'Opt_param_class(Max_f)',
                             'Opt_param_cl_after_reg(N_est)', 'Opt_param_cl_after_reg(Max_f)'])

result = result.groupby(['thre']).mean()


Unnamed: 0  Number  thre  Opt_param_class(N_est)  Opt_param_class(Max_f)  \
0            0       1   5.0                   500.0                    32.0   
1            1       2   5.0                   500.0                    32.0   
2            2       3   5.0                   101.0                    32.0   
3            3       4   5.0                   300.0                    32.0   
4            4       5   5.0                   500.0                    32.0   
5            5       1   5.5                   300.0                   256.0   
6            6       2   5.5                   300.0                    32.0   
7            7       3   5.5                   500.0                    32.0   
8            8       4   5.5                   300.0                    32.0   
9            9       5   5.5                   500.0                   512.0   
10          10       1   6.0                   101.0                   256.0   
11          11       2   6.0                   500.0                   256.0   
12          12       3   6.0                   500.0                   256.0   
13          13       4   6.0                   500.0                   256.0   
14          14       5   6.0                   500.0                   256.0   
15          15       1   6.5                   300.0                   768.0   
16          16       2   6.5                   300.0                   512.0   
17          17       3   6.5                   500.0                   512.0   
18          18       4   6.5                   101.0                   512.0   
19          19       5   6.5                   500.0                   256.0   
20          20       1   7.0                   300.0                   512.0   
21          21       2   7.0                   101.0                   768.0   
22          22       3   7.0                   101.0                   768.0   
23          23       4   7.0                   300.0                   768.0   
24          24       5   7.0                   300.0                   512.0   

    MCC(clas.)  Opt_param_cl_after_reg(N_est)  Opt_param_cl_after_reg(Max_f)  \
0     0.807880                          101.0                          768.0   
1     0.806623                          500.0                          768.0   
2     0.798916                          300.0                          768.0   
3     0.796601                          500.0                          512.0   
4     0.807880                          300.0                          768.0   
5     0.859249                          500.0                          256.0   
6     0.797512                          101.0                          256.0   
7     0.794055                          500.0                          256.0   
8     0.784671                          500.0                          256.0   
9     0.848035                          500.0                          256.0   
10    0.809642                          101.0                          512.0   
11    0.821197                          500.0                          256.0   
12    0.818176                          500.0                          512.0   
13    0.838954                          500.0                          512.0   
14    0.818176                          500.0                          256.0   
15    0.734591                          500.0                          256.0   
16    0.784237                          300.0                           32.0   
17    0.782623                          300.0                          256.0   
18    0.797827                          300.0                           32.0   
19    0.791441                          300.0                          768.0   
20    0.776149                          101.0                           32.0   
21    0.750827                          101.0                           32.0   
22    0.726769                          101.0                           32.0   
23 

RESULT TABLE:

In [4]:
display(result)

MCC(clas.)  MCC(class_after_reg.)
thre                                   
5.0     0.803580               0.806243
5.5     0.816704               0.866064
6.0     0.821229               0.853631
6.5     0.778144               0.817833
7.0     0.764956               0.799759